In [0]:
from pyspark.sql.functions import to_date,col
from pyspark.sql.types import LongType, StringType, StructField, StructType, BooleanType, ArrayType, IntegerType, DoubleType, FloatType, TimestampType
import pyspark.sql.functions as F
from pyspark.sql import Window
from pprint import pprint as pp
import json
from urllib.request import  urlopen
import requests

#Set prior

##mean

In [0]:
PriorMeanDf = spark.createDataFrame(
    [
        (1,0.001835,-0.5000,29.96,34.11),
        (2,0.002745,-0.78,22.52,44.26),
        (3,0.002997,0.0000,22.54,48.41)
    ],
    ['parity','decay','offset','ramp','scale']  # add your column names here
)

PriorMeanDf = PriorMeanDf.\
    withColumn('means', F.struct(col('decay'),col('offset'),col('ramp'),col('scale'))).\
    select('parity','means')

PriorMeanDf.display()

parity means 1 List(0.001835, -0.5, 29.96, 34.11) 2 List(0.002745, -0.78, 22.52, 44.26) 3 List(0.002997, 0.0, 22.54, 48.41)

##sd

In [0]:
PriorSdDf12 = spark.createDataFrame(
    [
        (1, 'sd',0.000738,0.002,1.530,6.891,1.91,1,'parity'),
        (2, 'sd',0.000979,0.007,0.9999,9.570,2.19,2,'parity')
        
    ],
    ['parity','type','decay','offset','ramp','scale','seMilk', 'equal','stratum']  # add your column names here
)

PriorSdDf12 = PriorSdDf12.\
    withColumn('sd', F.struct(col('decay'),col('offset'),col('ramp'),col('scale'))).\
    withColumn('discriminator',F.struct('equal','stratum')).\
    select('parity','discriminator','sd','seMilk')

PriorSdDf12.display()

parity discriminator sd seMilk 1 List(1, parity) List(7.38E-4, 0.002, 1.53, 6.891) 1.91 2 List(2, parity) List(9.79E-4, 0.007, 0.9999, 9.57) 2.19

In [0]:
PriorSdDf3 = spark.createDataFrame(
    [
        (3, 'sd',0.000972,0.03,8.724,10.66,2.14,3,'parity')
        
    ],
    ['parity','type','decay','offset','ramp','scale','seMilk','lowerLimit','stratum']  # add your column names here
)

PriorSdDf3 = PriorSdDf3.\
    withColumn('sd', F.struct(col('decay'),col('offset'),col('ramp'),col('scale'))).\
    withColumn('discriminator',F.struct('lowerLimit','stratum')).\
    select('parity','discriminator','sd','seMilk')
               
PriorSdDf3.display()

parity discriminator sd seMilk 3 List(3, parity) List(9.72E-4, 0.03, 8.724, 10.66) 2.14

##PriorTree

In [0]:
PriorTree12 = PriorMeanDf.\
    filter('parity!=3').\
    join(PriorSdDf12,'parity').\
    withColumn('priors',F.struct('means','sd','seMilk')).\
    withColumn('node',F.struct('priors')).\
    withColumn('content',F.struct('node')).\
    withColumn('priorsTree',F.struct('content','discriminator')).\
    select('priorsTree','parity')

PriorTree12.\
    display()

priorsTree parity List(List(List(List(List(0.001835, -0.5, 29.96, 34.11), List(7.38E-4, 0.002, 1.53, 6.891), 1.91))), List(1, parity)) 1 List(List(List(List(List(0.002745, -0.78, 22.52, 44.26), List(9.79E-4, 0.007, 0.9999, 9.57), 2.19))), List(2, parity)) 2

In [0]:
PriorTree3 = PriorMeanDf.\
    filter('parity=3').\
    join(PriorSdDf3,'parity').\
    withColumn('priors',F.struct('means','sd','seMilk')).\
    withColumn('node',F.struct('priors')).\
    withColumn('content',F.struct('node')).\
    withColumn('priorsTree',F.struct('content','discriminator')).\
    select('priorsTree','parity').\
    withColumn('ParityGroup',F.lit('3+'))

PriorTree3.display()

priorsTree parity ParityGroup List(List(List(List(List(0.002997, 0.0, 22.54, 48.41), List(9.72E-4, 0.03, 8.724, 10.66), 2.14))), List(3, parity)) 3 3+

#Read data

In [0]:
# whole data
FittingData= spark. \
  read. \
  parquet('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/FittingData/')

In [0]:
# 31693777
FittingData.count()

Out[8]: 31693777

In [0]:
FittingData = FittingData.\
    withColumn('HerdIdentifier',FittingData['HerdIdentifier'].cast(StringType())).\
    withColumn('AnimalIdentifier',FittingData['AnimalIdentifier'].cast(StringType()))


In [0]:
FittingData.printSchema()

root
-- HerdIdentifier: string (nullable = true)
-- AnimalIdentifier: string (nullable = true)
-- DaysInMilk: integer (nullable = true)
-- TestDayMilkYield: double (nullable = true)
-- LactationNumber: integer (nullable = true)
-- LastDIM: integer (nullable = true)

In [0]:
FittingData.display()

HerdIdentifier AnimalIdentifier DaysInMilk TestDayMilkYield LactationNumber LastDIM 503 602 93 33.18257032542748 5 344 503 602 207 19.090147572229576 5 344 503 602 276 17.512732977386378 5 344 503 751 5 30.724951581746893 3 576 503 751 206 24.154774034719104 3 576 503 751 278 20.21356261267508 3 576 503 751 318 24.939908646619276 3 576 503 751 562 15.437831737856907 3 576 503 755 120 45.83192515075672 2 471 503 788 251 20.949849987995375 3 447 503 870 82 22.378233325729553 1 326 503 870 93 25.377085846132097 1 326 503 870 96 24.560588711033525 1 326 503 870 317 14.129914417811587 1 326 503 903 76 41.67824882007898 3 230 503 903 204 31.68576037163688 3 230 503 905 232 17.351008752582825 1 317 503 964 85 43.39796203593119 3 371 503 964 251 20.313528270709103 3 371 503 965 138 35.23828421929903 1 390 503 965 310 21.78079509836644 1 390 503 968 202 36.12321891368771 3 360 503 1088 45 32.637507201018025 1 329 503 1089 328 18.656968437459412 4 386 503 1095 40 34.99673577757662 1 328 503 1115 346 10.75353814815378 2 359 503 1127 51 37.84175419524503 2 381 503 1127 193 30.621993514511082 2 381 503 1127 230 31.848510638297867 2 381 503 1127 293 28.45839043523462 2 381 503 1127 322 20.829547098291275 2 381 503 1127 362 15.981887810400057 2 381 503 1165 90 26.39037496355943 1 302 503 1165 277 12.807228065221993 1 302 503 1180 185 30.442610092257134 1 332 503 1180 197 32.197198011134596 1 332 503 1180 248 27.036777970032773 1 332 503 1180 302 17.368839998376792 1 332 503 1186 134 36.1917353107393 2 386 503 1186 257 27.793041823999076 2 386 503 1254 398 30.61046669714737 2 553 503 1254 403 32.65429915363376 2 553 503 1277 65 38.40858233872 2 362 503 1298 43 46.79936978034991 3 370 503 1303 276 27.86581559975208 2 370 503 1310 82 26.133040033220734 1 304 503 1348 73 45.98518195239541 2 394 503 1348 309 32.177607852271905 2 394 503 1349 3 13.306040475822648 3 255 503 1349 9 27.895476330314526 3 255 503 1349 102 38.57370941990419 3 255 503 1387 301 22.50105671411149 5 318 503 1387 305 19.83886183975103 5 318 503 1394 69 47.71874203866731 3 320 503 1394 114 30.32021957913998 3 320 503 1481 97 47.271048112194336 4 272 503 1481 234 32.14757658868559 4 272 503 1481 241 34.068581939404794 4 272 503 1493 168 44.04129721851088 3 324 503 1493 274 35.09855117350264 3 324 503 1493 103 43.400617957779055 4 441 503 1493 249 32.01869404204615 4 441 503 1496 75 41.38478261570767 2 313 503 1497 76 38.23049644128747 4 294 503 1497 160 32.715245353495796 4 294 503 1559 148 36.346680182463246 1 322 503 1560 62 49.845402030135304 4 459 503 1560 88 45.9900844164545 4 459 503 1560 138 44.31115436251146 4 459 503 1560 215 32.88246148564562 4 459 503 1587 120 33.93061648383454 1 477 503 1641 76 49.472697293976914 3 511 503 1641 270 36.15335774242904 3 511 503 1641 473 17.49952019078031 3 511 503 1732 228 38.971772237850416 2 422 503 1732 258 38.016348146442546 2 422 503 1732 334 32.94568834245108 2 422 503 1750 10 39.53611756409827 3 425 503 1750 166 41.9665496508325 3 425 503 1750 168 42.848372272116315 3 425 503 1750 192 39.569685271322875 3 425 503 1750 411 12.338604730869541 3 425 503 1793 86 27.2652892076017 1 595 503 1793 96 31.219469786295292 1 595 503 1793 393 23.491352071838605 1 595 503 2226 112 37.10303426550566 1 289 503 2248 297 32.44420491457037 1 397 503 2289 78 36.921195569097826 1 331 503 2289 179 35.033187209734045 1 331 503 2289 228 30.092213794476024 1 331 503 2289 309 15.633874317360206 1 331 504 972 40 40.73663039749211 3 342 504 972 51 37.45803535035386 3 342 504 981 100 48.99914892263151 4 343 504 981 295 31.70997863261826 4 343 504 989 36 31.512015194472735 1 415 504 1083 57 27.404697551749642 1 326 504 1083 58 26.405700169193985 1 326 504 1083 123 32.783018003992744 1 326 504 1083 179 32.134136117673954 1 326 504 1083 188 32.9646861138464 1 326 504 1083 316 17.496449584094144 1 326 504 1100 147 34.83822721586476 4 501 504 1100 348 18.166748822899493 4 501 504 1100 485 14.164239953407105 4 501 504 1416 104 38.51155925472533 3 294 504 1416 1

##Parity1&2

In [0]:
FittingData12 = FittingData.\
    filter('LactationNumber<3').\
    withColumnRenamed('HerdIdentifier','name').\
    withColumnRenamed('LactationNumber','parity').\
    withColumnRenamed('DaysInMilk','dim').\
    withColumnRenamed('TestDayMilkYield','milk').\
    withColumn('dayFraction', F.lit(1)).\
    withColumn('lacKey', F.concat(col('name'),F.lit("_"),col('AnimalIdentifier'), F.lit("_"), col('parity'))).\
    withColumn('Tuple', F.struct(col('dim'),col('milk'),col('dayFraction'))).\
    groupBy('name','AnimalIdentifier','lacKey','parity').\
    agg(F.array_sort(F.collect_list('Tuple')).alias('points')).\
    withColumn('lac', F.struct(col('lacKey'),col('parity'),col('points'))).\
    groupBy('name','AnimalIdentifier','parity').\
    agg(F.collect_list('lac').alias('lactations')).\
    withColumn('lactationSet', F.struct(col('name'),col('lactations'))).\
    withColumn('steppedFit',F.lit('true').cast(BooleanType())).\
    withColumn('returnInputData',F.lit('false').cast(BooleanType())).\
    withColumn('returnPriors',F.lit('false').cast(BooleanType())).\
    withColumn('returnPath',F.lit('false').cast(BooleanType())).\
    withColumn('fitMethod',F.lit('MilkBot@2.01')).\
    withColumn('preferredMilkUnit',F.lit('Kg')).\
    withColumn('options',F.struct(col('steppedFit'),col('returnInputData'),col('returnPriors'),col('returnPath'),col('fitMethod'),col('preferredMilkUnit'))).\
    join(PriorTree12,['parity']).\
    withColumn('fittingJob',F.struct(col('lactationSet'),col('options'),col('priorsTree'))).\
    withColumn('Json',F.struct(col('fittingJob'))).\
    select('name','AnimalIdentifier','parity','Json').\
    withColumn('json',F.to_json(col('Json')))

In [0]:
FittingData12.\
    display()

name AnimalIdentifier parity json 1006 1002 1 {"fittingJob":{"lactationSet":{"name":"1006","lactations":[{"lacKey":"1006_1002_1","parity":1,"points":[{"dim":1,"milk":23.104233045061445,"dayFraction":1},{"dim":2,"milk":15.095240124430049,"dayFraction":1},{"dim":3,"milk":15.999566105056811,"dayFraction":1},{"dim":4,"milk":18.023102530152947,"dayFraction":1},{"dim":5,"milk":19.411575906708038,"dayFraction":1},{"dim":6,"milk":20.192071070939384,"dayFraction":1},{"dim":7,"milk":20.648754002505918,"dayFraction":1},{"dim":8,"milk":20.17698141236669,"dayFraction":1},{"dim":9,"milk":23.878587784227058,"dayFraction":1},{"dim":10,"milk":23.950241645025933,"dayFraction":1},{"dim":11,"milk":23.82273090513295,"dayFraction":1},{"dim":12,"milk":24.543854115084564,"dayFraction":1},{"dim":13,"milk":24.695874528211007,"dayFraction":1},{"dim":14,"milk":25.465321046415415,"dayFraction":1},{"dim":15,"milk":26.961024700602998,"dayFraction":1},{"dim":16,"milk":27.137600006365396,"dayFraction":1},{"dim":17,"milk":28.663911151067307,"dayFraction":1},{"dim":18,"milk":29.764344918271757,"dayFraction":1},{"dim":19,"milk":28.736806189336207,"dayFraction":1},{"dim":20,"milk":27.522043753872552,"dayFraction":1},{"dim":21,"milk":28.37924480589929,"dayFraction":1},{"dim":22,"milk":28.738514809320083,"dayFraction":1},{"dim":23,"milk":29.924456418365516,"dayFraction":1},{"dim":24,"milk":31.01038433100542,"dayFraction":1},{"dim":25,"milk":31.952558609341658,"dayFraction":1},{"dim":26,"milk":31.466349780036754,"dayFraction":1},{"dim":27,"milk":30.433008697730394,"dayFraction":1},{"dim":28,"milk":30.261794382328876,"dayFraction":1},{"dim":29,"milk":29.64571260911024,"dayFraction":1},{"dim":30,"milk":30.89114908007975,"dayFraction":1},{"dim":31,"milk":29.93725685677441,"dayFraction":1},{"dim":32,"milk":29.57009276260373,"dayFraction":1},{"dim":33,"milk":28.475669202484127,"dayFraction":1},{"dim":34,"milk":28.896691071963616,"dayFraction":1},{"dim":35,"milk":29.008548330369145,"dayFraction":1},{"dim":36,"milk":28.589150618562236,"dayFraction":1},{"dim":37,"milk":29.856231308496085,"dayFraction":1},{"dim":38,"milk":31.54581049334378,"dayFraction":1},{"dim":39,"milk":32.069136281982814,"dayFraction":1},{"dim":40,"milk":32.69961340110929,"dayFraction":1},{"dim":41,"milk":32.71863796501793,"dayFraction":1},{"dim":42,"milk":32.02437714642522,"dayFraction":1},{"dim":43,"milk":32.190919149847474,"dayFraction":1},{"dim":44,"milk":31.894429345851435,"dayFraction":1},{"dim":45,"milk":31.622198902578855,"dayFraction":1},{"dim":46,"milk":33.30078626856468,"dayFraction":1},{"dim":47,"milk":32.763126916810805,"dayFraction":1},{"dim":48,"milk":31.984560726347645,"dayFraction":1},{"dim":49,"milk":32.4566472294664,"dayFraction":1},{"dim":50,"milk":31.90268268234255,"dayFraction":1},{"dim":51,"milk":32.1440393369528,"dayFraction":1},{"dim":52,"milk":34.5051346926626,"dayFraction":1},{"dim":53,"milk":35.22173840869331,"dayFraction":1},{"dim":54,"milk":33.831317333921135,"dayFraction":1},{"dim":55,"milk":34.230881070078524,"dayFraction":1},{"dim":56,"milk":34.22097361027956,"dayFraction":1},{"dim":57,"milk":33.97539255101266,"dayFraction":1},{"dim":58,"milk":33.619785655399845,"dayFraction":1},{"dim":59,"milk":32.81006341615553,"dayFraction":1},{"dim":60,"milk":32.90345099619457,"dayFraction":1},{"dim":61,"milk":33.14424960635041,"dayFraction":1},{"dim":62,"milk":33.53932094930056,"dayFraction":1},{"dim":63,"milk":33.73839256637276,"dayFraction":1},{"dim":64,"milk":33.78863271881943,"dayFraction":1},{"dim":65,"milk":34.675213753707965,"dayFraction":1},{"dim":66,"milk":34.69613801215448,"dayFraction":1},{"dim":67,"milk":35.498981853838124,"dayFraction":1},{"dim":68,"milk":34.9813400752431,"dayFraction":1},{"dim":69,"milk":34.335139505229776,"dayFraction":1},{"dim":70,"milk":34.68925597863522,"dayFraction":1},{"dim":71,"milk":33.79443198311123,"dayFraction":1},{"dim":72,"milk":33.1084683087296,"dayFraction":1},{"dim":73,"milk":33.58539461615735,"dayFraction":1},{"dim":74,"milk":32.3347297

In [0]:
# 62039
FittingData12.\
    count()

Out[16]: 62039

##Parity 3

In [0]:
FittingData3 = FittingData.\
    filter('LactationNumber>2').\
    withColumnRenamed('HerdIdentifier','name').\
    withColumnRenamed('LactationNumber','parity').\
    withColumnRenamed('DaysInMilk','dim').\
    withColumnRenamed('TestDayMilkYield','milk').\
    withColumn('dayFraction', F.lit(1)).\
    withColumn('lacKey', F.concat(col('name'),F.lit("_"),col('AnimalIdentifier'), F.lit("_"), col('parity'))).\
    withColumn('Tuple', F.struct(col('dim'),col('milk'),col('dayFraction'))).\
    groupBy('name','AnimalIdentifier','lacKey','parity').\
    agg(F.array_sort(F.collect_list('Tuple')).alias('points')).\
    withColumn('lac', F.struct(col('lacKey'),col('parity'),col('points'))).\
    groupBy('name','AnimalIdentifier','parity').\
    agg(F.collect_list('lac').alias('lactations')).\
    withColumn('lactationSet', F.struct(col('name'),col('lactations'))).\
    withColumn('steppedFit',F.lit('true').cast(BooleanType())).\
    withColumn('returnInputData',F.lit('false').cast(BooleanType())).\
    withColumn('returnPriors',F.lit('false').cast(BooleanType())).\
    withColumn('returnPath',F.lit('false').cast(BooleanType())).\
    withColumn('fitMethod',F.lit('MilkBot@2.01')).\
    withColumn('preferredMilkUnit',F.lit('Kg')).\
    withColumn('options',F.struct(col('steppedFit'),col('returnInputData'),col('returnPriors'),col('returnPath'),col('fitMethod'),col('preferredMilkUnit'))).\
    withColumn('ParityGroup',F.lit('3+')).\
    join(PriorTree3.drop('parity'),['ParityGroup']).\
    withColumn('fittingJob',F.struct(col('lactationSet'),col('options'),col('priorsTree'))).\
    withColumn('Json',F.struct(col('fittingJob'))).\
    select('name','AnimalIdentifier','parity','Json').\
    withColumn('json',F.to_json(col('Json')))


In [0]:
FittingData3.\
    display()

name AnimalIdentifier parity json 1006 1013 3 {"fittingJob":{"lactationSet":{"name":"1006","lactations":[{"lacKey":"1006_1013_3","parity":3,"points":[{"dim":3,"milk":23.983259548178623,"dayFraction":1},{"dim":4,"milk":20.826276740024845,"dayFraction":1},{"dim":5,"milk":23.077311348532007,"dayFraction":1},{"dim":6,"milk":23.183212278113487,"dayFraction":1},{"dim":7,"milk":25.276510017037044,"dayFraction":1},{"dim":8,"milk":26.75905954460721,"dayFraction":1},{"dim":9,"milk":28.496078122538982,"dayFraction":1},{"dim":10,"milk":29.239724996236262,"dayFraction":1},{"dim":11,"milk":29.776614362855817,"dayFraction":1},{"dim":12,"milk":29.535424976355934,"dayFraction":1},{"dim":13,"milk":31.386975215392024,"dayFraction":1},{"dim":14,"milk":31.21467150970369,"dayFraction":1},{"dim":15,"milk":30.68964717344406,"dayFraction":1},{"dim":16,"milk":31.454258711393017,"dayFraction":1},{"dim":17,"milk":31.736878132051082,"dayFraction":1},{"dim":18,"milk":31.733117964101467,"dayFraction":1},{"dim":19,"milk":32.14600823903635,"dayFraction":1},{"dim":20,"milk":32.611475668014066,"dayFraction":1},{"dim":21,"milk":33.611580217129074,"dayFraction":1},{"dim":22,"milk":33.53447874725258,"dayFraction":1},{"dim":23,"milk":33.86201883251906,"dayFraction":1},{"dim":24,"milk":33.463045720178755,"dayFraction":1},{"dim":25,"milk":33.83762264450514,"dayFraction":1},{"dim":26,"milk":34.8056936930084,"dayFraction":1},{"dim":27,"milk":36.10678595770417,"dayFraction":1},{"dim":28,"milk":34.5614640257076,"dayFraction":1},{"dim":29,"milk":35.350269063343205,"dayFraction":1},{"dim":30,"milk":34.40461130798829,"dayFraction":1},{"dim":31,"milk":34.96176899537182,"dayFraction":1},{"dim":32,"milk":35.510806080509724,"dayFraction":1},{"dim":33,"milk":35.21601077648418,"dayFraction":1},{"dim":34,"milk":34.20564135840253,"dayFraction":1},{"dim":35,"milk":35.559626095468154,"dayFraction":1},{"dim":36,"milk":35.086171332351086,"dayFraction":1},{"dim":37,"milk":36.52646781936511,"dayFraction":1},{"dim":38,"milk":35.72515239936326,"dayFraction":1},{"dim":39,"milk":34.80801576241049,"dayFraction":1},{"dim":40,"milk":36.47726992528787,"dayFraction":1},{"dim":41,"milk":35.96716424551178,"dayFraction":1},{"dim":42,"milk":36.77823415871018,"dayFraction":1},{"dim":43,"milk":35.487870964514684,"dayFraction":1},{"dim":44,"milk":36.64799352300885,"dayFraction":1},{"dim":45,"milk":36.83965510900005,"dayFraction":1},{"dim":46,"milk":36.914166620961986,"dayFraction":1},{"dim":47,"milk":35.984305910194934,"dayFraction":1},{"dim":48,"milk":38.54369566638342,"dayFraction":1},{"dim":49,"milk":38.70008800808371,"dayFraction":1},{"dim":50,"milk":36.44594147923128,"dayFraction":1},{"dim":51,"milk":38.17007848531435,"dayFraction":1},{"dim":52,"milk":38.91046488504076,"dayFraction":1},{"dim":53,"milk":38.552195870357345,"dayFraction":1},{"dim":54,"milk":38.22138287633176,"dayFraction":1},{"dim":55,"milk":37.429491214932085,"dayFraction":1},{"dim":56,"milk":35.93059423332333,"dayFraction":1},{"dim":57,"milk":36.135487977843056,"dayFraction":1},{"dim":58,"milk":36.71041701279282,"dayFraction":1},{"dim":59,"milk":37.600324739689036,"dayFraction":1},{"dim":60,"milk":38.72525997987253,"dayFraction":1},{"dim":61,"milk":38.083911463495205,"dayFraction":1},{"dim":62,"milk":38.25356300294089,"dayFraction":1},{"dim":63,"milk":38.58155351390048,"dayFraction":1},{"dim":64,"milk":38.234948693888676,"dayFraction":1},{"dim":65,"milk":40.44144801820759,"dayFraction":1},{"dim":66,"milk":39.64106463878327,"dayFraction":1},{"dim":67,"milk":38.08461640706383,"dayFraction":1},{"dim":68,"milk":38.59305301645338,"dayFraction":1},{"dim":69,"milk":37.52985578923452,"dayFraction":1},{"dim":70,"milk":37.13012020072354,"dayFraction":1},{"dim":71,"milk":39.01716890724378,"dayFraction":1},{"dim":72,"milk":40.01504541425585,"dayFraction":1},{"dim":73,"milk":38.26145815041268,"dayFraction":1},{"dim":74,"milk":38.43105539830165,"dayFraction":1},{"dim":75,"milk":39.094360500071986,"dayFraction":1},{"dim":76,"milk":38.0291168639891

In [0]:
# 50910
FittingData3.count()

Out[19]: 50910

## combined

In [0]:
FittingDataFinal = FittingData12.\
    unionAll(FittingData3).\
    cache()

In [0]:
FittingDataFinal.write.\
    mode("overwrite"). \
    parquet('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/FinalDataMiel/')

In [0]:
FittingDataFinal = spark.read.\
  parquet('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/FinalDataMiel/')

In [0]:
# should be 112949
FittingDataFinal.count()

Out[36]: 112949

# Fitting

Version Miel

In [0]:
headers = {
    'Content-type': 'application/json',
    'X-API-KEY': '00baNEuQtjm51nvL'
}

In [0]:
def getMilkbotData(row):
    response = requests.post('https://europe-west1-numeric-analogy-337601.cloudfunctions.net/milkBot-fitter/fitlactations', headers=headers, data=row)
    return response.text


In [0]:
""" Converting function to UDF """
milkbotUDF = udf(lambda z: getMilkbotData(z),StringType())


## herd by herd

In [0]:
FittingDataFinal = spark.read.\
  parquet('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/0405Split/FinalDataMiel/')

In [0]:
FittingDataFinal.display()

name AnimalIdentifier parity json 1121 1202 1 {"fittingJob":{"lactationSet":{"name":"1121","lactations":[{"lacKey":"1121_1202_1","parity":1,"points":[{"dim":7,"milk":7.935706084959818,"dayFraction":1},{"dim":8,"milk":9.65669319880983,"dayFraction":1},{"dim":9,"milk":8.07509133757563,"dayFraction":1},{"dim":10,"milk":7.671513427157629,"dayFraction":1},{"dim":11,"milk":8.436669719701154,"dayFraction":1},{"dim":12,"milk":7.950694526668703,"dayFraction":1},{"dim":13,"milk":8.227744300837482,"dayFraction":1},{"dim":14,"milk":8.356462960408333,"dayFraction":1},{"dim":15,"milk":7.834327495342173,"dayFraction":1},{"dim":16,"milk":8.098082106067562,"dayFraction":1},{"dim":17,"milk":7.787324458580128,"dayFraction":1},{"dim":18,"milk":7.709355022520986,"dayFraction":1},{"dim":19,"milk":8.333665934943127,"dayFraction":1},{"dim":20,"milk":8.018499812848345,"dayFraction":1},{"dim":21,"milk":8.02704168033253,"dayFraction":1},{"dim":22,"milk":8.404579664413792,"dayFraction":1},{"dim":23,"milk":9.378253046416713,"dayFraction":1},{"dim":24,"milk":9.468845305100295,"dayFraction":1},{"dim":25,"milk":8.740401472579029,"dayFraction":1},{"dim":26,"milk":9.484036175590447,"dayFraction":1},{"dim":27,"milk":8.430737062205962,"dayFraction":1},{"dim":28,"milk":8.848740191524003,"dayFraction":1},{"dim":29,"milk":8.011161167430469,"dayFraction":1},{"dim":30,"milk":8.8722927557879,"dayFraction":1},{"dim":31,"milk":7.831386204594001,"dayFraction":1},{"dim":32,"milk":8.13221187354292,"dayFraction":1},{"dim":33,"milk":7.9799473220859305,"dayFraction":1},{"dim":34,"milk":8.402455983109341,"dayFraction":1},{"dim":35,"milk":9.453918786067055,"dayFraction":1}]}]},"options":{"steppedFit":true,"returnInputData":false,"returnPriors":false,"returnPath":false,"fitMethod":"MilkBot@2.01","preferredMilkUnit":"Kg"},"priorsTree":{"content":{"node":{"priors":{"means":{"decay":0.001835,"offset":-0.5,"ramp":29.96,"scale":34.11},"sd":{"decay":7.38E-4,"offset":0.002,"ramp":1.53,"scale":6.891},"seMilk":1.91}}},"discriminator":{"equal":1,"stratum":"parity"}}}} 506 1449 3 {"fittingJob":{"lactationSet":{"name":"506","lactations":[{"lacKey":"506_1449_3","parity":3,"points":[{"dim":1,"milk":3.522636541238427,"dayFraction":1},{"dim":2,"milk":12.406702208682411,"dayFraction":1},{"dim":3,"milk":17.4540307002669,"dayFraction":1},{"dim":4,"milk":28.380602710340135,"dayFraction":1},{"dim":5,"milk":32.165148465986206,"dayFraction":1},{"dim":6,"milk":33.34419249096008,"dayFraction":1},{"dim":7,"milk":37.321640903686095,"dayFraction":1},{"dim":8,"milk":39.76942269637787,"dayFraction":1},{"dim":9,"milk":38.417990973085125,"dayFraction":1},{"dim":10,"milk":42.705555389534695,"dayFraction":1},{"dim":11,"milk":41.1150418752659,"dayFraction":1},{"dim":12,"milk":43.20303001963901,"dayFraction":1},{"dim":13,"milk":45.53313509583733,"dayFraction":1},{"dim":14,"milk":43.9496731298414,"dayFraction":1},{"dim":15,"milk":42.82828016318778,"dayFraction":1},{"dim":16,"milk":43.449874363989466,"dayFraction":1},{"dim":17,"milk":43.72970295986428,"dayFraction":1},{"dim":18,"milk":46.69791746714823,"dayFraction":1},{"dim":19,"milk":47.24987662444482,"dayFraction":1},{"dim":20,"milk":48.50982636901354,"dayFraction":1},{"dim":21,"milk":48.71733345115779,"dayFraction":1},{"dim":22,"milk":50.08822634621235,"dayFraction":1},{"dim":23,"milk":52.58499909833678,"dayFraction":1},{"dim":24,"milk":52.354076997072056,"dayFraction":1},{"dim":25,"milk":53.246240574812205,"dayFraction":1},{"dim":26,"milk":52.7090106465853,"dayFraction":1},{"dim":27,"milk":53.693191848263154,"dayFraction":1},{"dim":28,"milk":51.75000706318886,"dayFraction":1},{"dim":29,"milk":51.98017002507022,"dayFraction":1},{"dim":30,"milk":50.57851239669422,"dayFraction":1},{"dim":31,"milk":53.74074687226545,"dayFraction":1},{"dim":32,"milk":55.88705781308713,"dayFraction":1},{"dim":33,"milk":55.35538397547702,"dayFraction":1},{"dim":34,"milk":55.54416532590148,"dayFraction":1},{"dim":35,"milk":57.120954247057306,"dayFraction":1},{"dim":36,"milk":55.5749187

In [0]:
herd = FittingDataFinal.\
    filter('name!=1006').\
    select('name').distinct().\
    rdd.flatMap(lambda x: x).collect()

In [0]:
len(herd)

Out[39]: 90

In [0]:
herd

Out[37]: ['1090',
 '718',
 '740',
 '711',
 '987',
 '672',
 '979',
 '1112',
 '724',
 '1483',
 '974',
 '1021',
 '710',
 '512',
 '1032',
 '924',
 '966',
 '1109',
 '951',
 '787',
 '712',
 '1070',
 '973',
 '964',
 '726',
 '928',
 '1010',
 '656',
 '1071',
 '503',
 '1152',
 '1106',
 '1052',
 '505',
 '658',
 '1061',
 '736',
 '716',
 '1128',
 '678',
 '657',
 '1113',
 '645',
 '722',
 '1069',
 '983',
 '709',
 '1148',
 '1107',
 '927',
 '506',
 '1138',
 '1068',
 '725',
 '965',
 '1018',
 '929',
 '741',
 '1080',
 '731',
 '708',
 '1050',
 '654',
 '950',
 '643',
 '992',
 '642',
 '1048',
 '715',
 '513',
 '945',
 '1085',
 '1088',
 '514',
 '705',
 '1086',
 '1075',
 '720',
 '721',
 '735',
 '676',
 '1121',
 '677',
 '925',
 '1047',
 '504',
 '717',
 '707',
 '946',
 '920']

In [0]:
for a in herd:
    FittingDataFinal.\
    filter(col('name')==a).\
    withColumn("result", milkbotUDF(col("json"))).\
    repartition(10).\
    write.\
    mode('overwrite').\
    json('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/0405Split/HerdByHerdFitting/' +a+'/')

# Read result

In [0]:
Result = spark.read.\
  json('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/0405Split/HerdByHerdFitting/*')

In [0]:
Result.count()

Out[2]: 112949

In [0]:
Result.display()

AnimalIdentifier json name parity result 3033 {"fittingJob":{"lactationSet":{"name":"504","lactations":[{"lacKey":"504_3033_3","parity":3,"points":[{"dim":1,"milk":9.509448914227853,"dayFraction":1},{"dim":2,"milk":18.569888609414303,"dayFraction":1},{"dim":3,"milk":22.79759040143381,"dayFraction":1},{"dim":4,"milk":26.892239970493957,"dayFraction":1},{"dim":5,"milk":29.674402642529273,"dayFraction":1},{"dim":6,"milk":35.1627172657769,"dayFraction":1},{"dim":7,"milk":36.47742386297244,"dayFraction":1},{"dim":8,"milk":37.328284607256066,"dayFraction":1},{"dim":9,"milk":37.94129998600158,"dayFraction":1},{"dim":10,"milk":40.74823075045889,"dayFraction":1},{"dim":11,"milk":43.761054818332134,"dayFraction":1},{"dim":12,"milk":44.88969621500398,"dayFraction":1},{"dim":13,"milk":47.51711383727573,"dayFraction":1},{"dim":14,"milk":47.25913448344391,"dayFraction":1},{"dim":15,"milk":48.103754940711454,"dayFraction":1},{"dim":16,"milk":49.05601341966492,"dayFraction":1},{"dim":17,"milk":48.18109779896157,"dayFraction":1},{"dim":18,"milk":49.839640563278365,"dayFraction":1},{"dim":19,"milk":49.51326286427802,"dayFraction":1},{"dim":20,"milk":50.36614902407751,"dayFraction":1},{"dim":21,"milk":52.543497612689166,"dayFraction":1},{"dim":22,"milk":53.02767748281569,"dayFraction":1},{"dim":23,"milk":54.49843359054688,"dayFraction":1},{"dim":24,"milk":54.83092293934442,"dayFraction":1},{"dim":25,"milk":53.589169288803845,"dayFraction":1},{"dim":26,"milk":52.14772918248252,"dayFraction":1},{"dim":27,"milk":51.68905350528806,"dayFraction":1},{"dim":28,"milk":53.297191476545436,"dayFraction":1},{"dim":29,"milk":53.83940309321117,"dayFraction":1},{"dim":30,"milk":55.5191174532653,"dayFraction":1},{"dim":31,"milk":55.98236365379085,"dayFraction":1},{"dim":32,"milk":54.05503340505038,"dayFraction":1},{"dim":33,"milk":55.96443990105969,"dayFraction":1},{"dim":34,"milk":57.13893451665889,"dayFraction":1},{"dim":35,"milk":58.56280774499277,"dayFraction":1},{"dim":36,"milk":58.54041268437146,"dayFraction":1},{"dim":37,"milk":58.66927632038825,"dayFraction":1},{"dim":38,"milk":58.238432054372296,"dayFraction":1},{"dim":39,"milk":56.29487719343361,"dayFraction":1},{"dim":40,"milk":57.85027038854679,"dayFraction":1},{"dim":41,"milk":56.9655699668412,"dayFraction":1},{"dim":42,"milk":55.40444903037844,"dayFraction":1},{"dim":43,"milk":56.65908894708066,"dayFraction":1},{"dim":44,"milk":55.703055780722764,"dayFraction":1},{"dim":45,"milk":51.986264633898244,"dayFraction":1},{"dim":46,"milk":49.99448349497287,"dayFraction":1},{"dim":47,"milk":47.14478838087976,"dayFraction":1},{"dim":48,"milk":47.10507526714683,"dayFraction":1},{"dim":49,"milk":52.05117276214591,"dayFraction":1},{"dim":50,"milk":50.831915919880174,"dayFraction":1},{"dim":51,"milk":52.97591421941266,"dayFraction":1},{"dim":52,"milk":53.02868080270358,"dayFraction":1},{"dim":53,"milk":52.514311676510665,"dayFraction":1},{"dim":54,"milk":50.8255984367367,"dayFraction":1},{"dim":55,"milk":54.18827939313348,"dayFraction":1},{"dim":56,"milk":51.97256515775034,"dayFraction":1},{"dim":57,"milk":53.69955375280793,"dayFraction":1},{"dim":58,"milk":52.02637958030046,"dayFraction":1},{"dim":59,"milk":51.52963758511952,"dayFraction":1},{"dim":60,"milk":46.507628096742174,"dayFraction":1},{"dim":61,"milk":43.697794462693565,"dayFraction":1},{"dim":62,"milk":41.94038615325143,"dayFraction":1},{"dim":63,"milk":38.64027131477245,"dayFraction":1},{"dim":64,"milk":39.537265671501046,"dayFraction":1},{"dim":65,"milk":40.62073688048592,"dayFraction":1},{"dim":66,"milk":41.64319558398252,"dayFraction":1},{"dim":67,"milk":42.77774142588733,"dayFraction":1},{"dim":68,"milk":44.80045974909716,"dayFraction":1},{"dim":69,"milk":48.048518905583435,"dayFraction":1},{"dim":70,"milk":48.57438518755167,"dayFraction":1},{"dim":71,"milk":50.10494907237121,"dayFraction":1},{"dim":72,"milk":49.632203139609274,"dayFraction":1},{"dim":73,"milk":48.72294312913225,"dayFraction":1},{"dim":74,"milk":49.41478990987946,"dayFraction":

## format

In [0]:
from pyspark.sql import types as T

schema = T.ArrayType(T.StructType([
    T.StructField('lacKey', T.StringType()),
    T.StructField('n', T.IntegerType()),
    T.StructField('params', T.StructType([
        StructField('scale', FloatType(), True),
        StructField('ramp', FloatType(), True),
        StructField('decay', FloatType(), True),
        StructField('offset', FloatType(), True),
    ])),
    T.StructField('sdResiduals', T.FloatType()),
]))

ResultFormatted = Result.\
    select(F.json_tuple('result','fits').alias('FittingResult')).\
    withColumn('temp',F.explode(F.from_json('FittingResult',schema=schema))).\
    select('temp.*','*').\
    drop('temp','FittingResult').\
    withColumn('Magnitude',col('params.scale')).\
    withColumn('TimeToPeakYield',col('params.ramp')).\
    withColumn('Offset',col('params.offset')).\
    withColumn('Decay',col('params.decay')).\
    drop('params').\
    withColumn('HerdIdentifier', F.split('lacKey','_').getItem(0)).\
    withColumn('AnimalIdentifier', F.split('lacKey','_').getItem(1)).\
    withColumn('LactationNumber', F.split('lacKey','_').getItem(2)).\
    drop('lacKey')

In [0]:
#The fitting result should have the same rows number with the test-day record number: 31,693,777
ResultFormatted.count()

Out[9]: 31693041

In [0]:
ResultFormatted.display()

n sdResiduals Magnitude TimeToPeakYield Offset Decay HerdIdentifier AnimalIdentifier LactationNumber 1 0.0 23.898785 22.7552 -0.775189 0.00218413 504 3033 3 2 4.266536 28.33078 22.772387 -0.7740984 0.00218413 504 3033 3 3 5.0760984 32.106182 22.738012 -0.7740984 0.002173271 504 3033 3 4 5.753261 35.55329 22.686451 -0.7740984 0.002162412 504 3033 3 5 6.145131 38.507954 22.617702 -0.7730078 0.0021298355 504 3033 3 6 7.0152526 42.283356 22.548954 -0.7708266 0.00218413 504 3033 3 7 7.362221 44.25313 22.480206 -0.7708266 0.0020212468 504 3033 3 8 7.419791 46.058758 22.256775 -0.76973605 0.0019560931 504 3033 3 9 7.339554 47.536095 22.170837 -0.7686454 0.0019017991 504 3033 3 10 7.3905663 48.849277 22.016155 -0.76755476 0.0018040688 504 3033 3 11 7.556802 50.490757 21.895845 -0.764283 0.0017063387 504 3033 3 12 7.6605754 51.80394 21.930218 -0.75773937 0.0016629033 504 3033 3 13 7.8783393 53.445423 22.205214 -0.7402898 0.0018366455 504 3033 3 14 7.778459 53.773716 21.39742 -0.75883 0.0012719834 504 3033 3 15 7.7312393 54.594456 21.277115 -0.7566488 0.0011416763 504 3033 3 16 7.6696744 55.415195 21.225557 -0.75337696 0.0010113696 504 3033 3 17 7.5233655 55.743492 21.10525 -0.75337696 8.702041E-4 504 3033 3 18 7.3992553 56.23593 20.967745 -0.7511958 7.073207E-4 504 3033 3 19 7.2691603 56.56423 20.984934 -0.7490146 6.2044983E-4 504 3033 3 20 7.155993 57.056675 21.105236 -0.7402898 5.770147E-4 504 3033 3 21 7.0453086 57.22082 20.881804 -0.74574274 3.3811864E-4 504 3033 3 22 6.949094 57.549118 20.864618 -0.74465215 1.8609424E-4 504 3033 3 23 6.9143953 58.205715 21.122425 -0.7402898 1.4265827E-4 504 3033 3 24 6.7787933 58.041565 20.813066 -0.7413804 -1.9396705E-4 504 3033 3 25 6.76258 58.862312 21.397419 -0.7402898 2.3210669E-5 504 3033 3 26 6.527111 58.369858 20.864618 -0.7359274 -3.1341478E-4 504 3033 3 27 6.4208183 58.698154 21.03649 -0.731565 -2.4826147E-4 504 3033 3 28 6.4998803 59.683044 21.930222 -0.7228402 2.729653E-4 504 3033 3 29 6.388712 59.683044 22.205214 -0.7359274 9.922305E-5 504 3033 3 30 6.0647655 58.534008 20.916182 -0.7359274 -5.740281E-4 504 3033 3 31 6.0580316 59.02645 21.380232 -0.7359274 -4.220037E-4 504 3033 3 32 5.9596834 59.02645 21.311483 -0.7359274 -4.220037E-4 504 3033 3 33 5.779907 58.69816 21.002117 -0.7370179 -7.3691143E-4 504 3033 3 34 5.691117 58.69816 21.019302 -0.73592734 -8.3464145E-4 504 3033 3 35 5.6512914 58.8623 21.208363 -0.7337462 -8.563595E-4 504 3033 3 36 6.255683 65.92066 24.405157 -0.70430005 0.001489161 504 3033 3 37 5.8956084 61.98111 23.855167 -0.70539063 5.5787343E-5 504 3033 3 38 5.4062057 58.8623 21.311481 -0.73374623 -0.0011386902 504 3033 3 39 5.835558 61.981113 23.580183 -0.72284025 2.7296535E-4 504 3033 3 40 5.621091 61.652813 23.683298 -0.70539063 -1.8310826E-4 504 3033 3 41 5.7226315 62.63772 24.405157 -0.70539063 2.6210732E-4 504 3033 3 42 5.3042374 60.01133 22.273952 -0.70539063 -6.826171E-4 504 3033 3 43 5.242334 60.01133 22.273952 -0.70539063 -6.826171E-4 504 3033 3 44 5.3415112 61.160385 23.167692 -0.72284025 -2.3740277E-4 504 3033 3 45 5.2164674 60.01133 21.792715 -0.70539063 -4.6543966E-4 504 3033 3 46 5.3000064 60.01133 21.448975 -0.72720265 -2.4826202E-4 504 3033 3 47 5.752107 62.30941 23.030197 -0.72284025 9.679341E-4 504 3033 3 48 5.8124437 61.98112 23.098938 -0.7075718 8.810651E-4 504 3033 3 49 5.7881927 61.98112 22.961441 -0.70539063 9.896541E-4 504 3033 3 50 5.736854 61.488667 21.792727 -0.72284025 0.0011416766 504 3033 3 51 6.03648 64.77162 23.442682 -0.70539063 0.0025316146 504 3033 3 52 5.9782453 64.77162 23.442682 -0.70539063 0.0025316146 504 3033 3 53 5.548645 60.50379 21.191175 -0.72284025 9.0278196E-4 504 3033 3 54 5.52161 60.503777 20.7615 -0.73156506 0.0010548055 504 3033 3 55 5.550153 61.488667 21.51773 -0.72284013 0.0014022903 504 3033 3 56 5.4509506 60.50379 20.898994 -0.72284025 0.0010873834 504 3033 3 57 5.382758 60.175484 20.417755 -0.731565 0.001076524 504 3033 3 58 5.5248303 62.80185 21.930223 -0.72284025 0.0020103883 504 3033 3 59 5.315863 60.011333 

In [0]:
ResultFormatted .\
  agg(F.count('*').alias('NumbersOfRecord'),
        F.countDistinct("HerdIdentifier").alias('NumbersOfHerds'),
        F.countDistinct("HerdIdentifier","AnimalIdentifier").alias('NumberOfCows')).\
    display()

NumbersOfRecord NumbersOfHerds NumberOfCows 31693041 91 42894

In [0]:
ResultFormatted.write.\
    mode("overwrite"). \
    parquet('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/0405Split/FittingResult/')

In [0]:
ResultFormatted=Result

In [0]:
Result = spark. \
  read. \
  parquet('wasbs://gpluse-cluster-2@bovianalytics.blob.core.windows.net/Projects/ChenYoungYan/11022022/Output/0405Split/FittingResult/')